In [ ]:
import pandas as pd
import numpy as np
from analytics.basket_index import MarkitBasketIndex
import matplotlib.pyplot as plt

from utils.db import dbengine
from ipywidgets import widgets
engine = dbengine('serenitasdb')

In [ ]:
w = widgets.Dropdown(
    options=['IG', 'HY', 'EU', 'XO'],
    value='IG',
    description='Index:',
    disabled=False,
)
w

In [ ]:
w_1 = widgets.IntSlider(value=32, min=22, max=32, description = 'Series')
w_1

In [ ]:
value_date = (pd.datetime.today() - pd.offsets.BDay(2)).date()
index_type = w.value
series = w_1.value

In [ ]:
sql_string = "select * from index_members(%s, %s)"
df = pd.read_sql_query(sql_string, engine, params=(index_type + str(series), value_date), index_col=['markit_ticker'])
df1 = pd.read_sql_query(sql_string, engine, params=(index_type + str(series-2), value_date), index_col=['markit_ticker'])

In [ ]:
#Removals
df1.loc[df1.index.difference(df.index)]

In [ ]:
#Additions
df.loc[df.index.difference(df1.index)]

In [ ]:
date_range = pd.bdate_range(value_date - 52 * pd.offsets.Week(), value_date, freq='5B')
index = MarkitBasketIndex(index_type, series, ['5yr'])
default_prob = {}
for d in date_range:
    index.value_date = d
    surv_prob, tickers = index.survival_matrix()
    default_prob[d] = pd.Series(1 - np.ravel(surv_prob), index=tickers)
default_prob = pd.concat(default_prob)

In [ ]:
#Top 20 highest cumulative
top20 = default_prob.unstack(-1)[default_prob[value_date].nlargest(20).index]
top20.index.name='date'
top20.columns.name='tickers'
ax = top20.plot(title=f'market implied default probabilities to {index.maturities[0]}', figsize=(10,6))
ax.legend(loc='upper center', bbox_to_anchor=(1.3, 1), ncol=1)
ax.set(xlabel='date', ylabel='probability')
plt.tight_layout()